In [1]:
import torch
import torch.nn as nn
from transformers import ElectraTokenizer, ElectraForSequenceClassification
from torch.utils.data import DataLoader, Dataset
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np
from tqdm import tqdm 

In [2]:
# 데이터셋 클래스 정의
class CustomDataset(Dataset):
    def __init__(self, sentences, labels, tokenizer, max_length):
        self.sentences = sentences
        self.labels = labels
        self.tokenizer = tokenizer
        self.max_length = max_length

    def __len__(self):
        return len(self.sentences)

    def __getitem__(self, idx):
        sentence = self.sentences[idx]
        label = self.labels[idx]

        encoding = self.tokenizer.encode_plus(
            sentence,
            add_special_tokens=True,
            max_length=self.max_length,
            return_token_type_ids=False,
            padding='max_length',
            return_attention_mask=True,
            return_tensors='pt',
        )

        return {
            'input_ids': encoding['input_ids'].squeeze(),
            'attention_mask': encoding['attention_mask'].squeeze(),
            'labels': torch.tensor(label, dtype=torch.long),
        }

In [3]:
# 예시 데이터로 대체 (이후 실제 데이터셋으로 변경해야 합니다)
dataset = pd.read_csv("../dataset/primary_classification_data2.csv", encoding='UTF-8')
dataset

sentence sentiment
0       언니 동생으로 부르는게 맞는 일인가요        부정
1                그냥 내 느낌일뿐겠지        부정
2              아직너무초기라서 그런거죠        부정
3              유치원버스 사고 낫다던데        부정
4                근데 원래이런거맞나요        부정
...                      ...       ...
526124           마라톤 기록 갱신했어        중립
526125           많이 몰려있긴 하던데        중립
526126         나 요즘 주식을 시작했어        중립
526127            하고 싶어 추천해줘        중립
526128             걱정해줘서 고마워        중립

[526129 rows x 2 columns]

In [4]:
dataset.isnull().sum()

sentence     0
sentiment    0
dtype: int64

In [5]:
# 데이터 프레임에서 한국어 문장과 라벨을 가져옵니다.
sentences = dataset['sentence'].values
labels = dataset['sentiment'].values

In [6]:
# 라벨을 One-Hot 인코딩으로 변환합니다.
label_map = {'부정': 0, '중립': 1, '긍정': 2}
labels = np.array([label_map[label] for label in labels])

In [7]:
# koELECTRA 토크나이저 불러오기
tokenizer = ElectraTokenizer.from_pretrained("koelectra-base-v3-discriminator")

In [8]:
# 문장을 토큰화하고 시퀀스로 변환했을 때의 길이 출력
length = [len(tokenizer.encode(sentence)) for sentence in tqdm(sentences)]

100%|██████████| 526129/526129 [02:11<00:00, 3986.35it/s]


In [9]:
len(length)

526129

In [11]:
import plotly.graph_objects as go

dataset['length'] = length

# 히스토그램 생성
histogram = go.Histogram(x=dataset['length'], nbinsx=20)

# 최댓값과 최솟값 계산
max_value = dataset['length'].max()
min_value = dataset['length'].min()

# 최댓값과 최솟값을 주석으로 추가하여 표시
annotations = [
    {
        'x': max_value,
        'y': 0,
        'xref': 'x',
        'yref': 'y',
        'text': f'Max: {max_value}',
        'showarrow': True,
        'arrowhead': 4,
        'ax': 0,
        'ay': -40
    },
    {
        'x': min_value,
        'y': 0,
        'xref': 'x',
        'yref': 'y',
        'text': f'Min: {min_value}',
        'showarrow': True,
        'arrowhead': 4,
        'ax': 0,
        'ay': -40
    }
]

# 그래프 생성 및 레이아웃 설정
fig = go.Figure(histogram)
fig.update_layout(annotations=annotations)

# 그래프 출력
fig.show()

In [13]:
len([i for i in length if i <= 60])/len(length) # 패딩 최대길이를 산정하기 위함. 60으로 설정하면 약 95%커버가능

0.9571112787928436

In [8]:
# 문장을 토큰화하고 시퀀스로 변환합니다.
sequences = [tokenizer.encode(sentence, padding='max_length', max_length=60, truncation=True) for sentence in tqdm(sentences)]

100%|██████████| 526129/526129 [02:18<00:00, 3803.93it/s]


In [9]:
# 학습 데이터와 검증 데이터로 나눕니다.
train_sequences, val_sequences, train_labels, val_labels = train_test_split(
    sequences, labels, test_size=0.2, random_state=42
)

In [10]:
# 데이터셋과 데이터로더 생성
train_dataset = CustomDataset(train_sequences, train_labels, tokenizer, max_length=32)
train_dataloader = DataLoader(train_dataset, batch_size=64, shuffle=True)

val_dataset = CustomDataset(val_sequences, val_labels, tokenizer, max_length=32)
val_dataloader = DataLoader(val_dataset, batch_size=64, shuffle=False)

In [11]:
# koELECTRA 모델 불러오기
model = ElectraForSequenceClassification.from_pretrained("koelectra-base-v3-discriminator", num_labels=3)

Some weights of the model checkpoint at koelectra-base-v3-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense.weight', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at koelectra-base-v3-discriminator and are newly initialized: ['classifier.out_p

In [12]:
# 변경하고자 하는 Dropout 비율
new_dropout_rate = 0.2

# 기존의 Dropout 비율 변경
for name, module in model.electra.named_children():
    if "dropout" in name:
        module.p = new_dropout_rate

In [23]:
# 모델 구조 확인
# print(model)
# from torchsummary import summary
# 입력 데이터의 형태를 지정 (예: 배치 크기 1, 시퀀스 길이 128)
# input_shape = (1, 128)

# # 모델 구조 요약 출력
# summary(model, input_shape)

In [13]:
# 학습 함수 정의 (tqdm을 사용하여 진행 상황 및 지표 시각화)
def train_fn(data_loader, model, optimizer, device):
    model.train()
    progress_bar = tqdm(data_loader, desc="Training")
    
    train_losses = []  # train_loss 기록을 위한 리스트
    train_accs = []  # train_accuracy 기록을 위한 리스트

    for batch in progress_bar:
        input_ids = batch['input_ids'].to(device)
        attention_mask = batch['attention_mask'].to(device)
        labels = batch['labels'].to(device)

        optimizer.zero_grad()
        outputs = model(input_ids=input_ids, attention_mask=attention_mask, labels=labels)
        loss = outputs.loss
        logits = outputs.logits

        loss.backward()
        optimizer.step()
        
        # 정확도 계산
        predicted_labels = torch.argmax(logits, dim=1)
        accuracy = (predicted_labels == labels).float().mean().item()
        
        train_losses.append(loss.item())
        train_accs.append(accuracy)
        progress_bar.set_postfix({'Loss': loss.item(), 'Accuracy': accuracy})

    return train_losses, train_accs

In [14]:
# 평가 함수 정의
def eval_fn(data_loader, model, device):
    model.eval()
    correct_predictions = 0
    total_predictions = 0
    predicted_labels_list = []  # 예측한 라벨들을 저장하기 위한 리스트
    true_labels_list = []  # 실제 라벨들을 저장하기 위한 리스트

    with torch.no_grad():
        for batch in data_loader:
            input_ids = batch['input_ids'].to(device)
            attention_mask = batch['attention_mask'].to(device)
            labels = batch['labels'].to(device)

            outputs = model(input_ids=input_ids, attention_mask=attention_mask)
            logits = outputs.logits

            predicted_labels = torch.argmax(logits, dim=1)
            correct_predictions += (predicted_labels == labels).sum().item()
            total_predictions += labels.size(0)

            # 예측한 라벨과 실제 라벨을 리스트에 추가
            predicted_labels_list.extend(predicted_labels.tolist())
            true_labels_list.extend(labels.tolist())

    accuracy = correct_predictions / total_predictions

    # 예측한 라벨과 실제 라벨 출력
    predicted_labels_list = np.array(predicted_labels_list)
    true_labels_list = np.array(true_labels_list)
    print("Predicted Labels:", predicted_labels_list)
    print("True Labels:", true_labels_list)

    return accuracy

In [15]:
# 장치 설정 (GPU 사용을 위해)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
model.to(device)
# 옵티마이저와 손실 함수 설정
optimizer = torch.optim.AdamW(model.parameters(), lr=1e-5)
loss_fn = torch.nn.CrossEntropyLoss()

In [16]:
# 학습 및 Early Stopping 정의
num_epochs = 2

def train_with_early_stopping(train_dataloader, val_dataloader, model, optimizer, loss_fn, device, patience=3):
    model.to(device)
    best_val_accuracy = 0.0
    best_model_state_dict = None
    no_improvement = 0

    for epoch in range(num_epochs):
        train_losses, train_accs = train_fn(train_dataloader, model, optimizer, loss_fn, device)
        val_loss, val_accuracy = eval_fn(val_dataloader, model, loss_fn, device)

        print(f"Epoch {epoch+1}/{num_epochs} - Train Loss: {np.mean(train_losses):.4f} - Train Accuracy: {np.mean(train_accs):.4f} - Validation Loss: {val_loss:.4f} - Validation Accuracy: {val_accuracy:.4f}")

        # Early Stopping 체크
        if val_accuracy > best_val_accuracy:
            best_val_accuracy = val_accuracy
            best_model_state_dict = model.state_dict()
            no_improvement = 0
        else:
            no_improvement += 1

        if no_improvement >= patience:
            print(f"No improvement in validation accuracy for {patience} epochs. Early stopping...")
            break

    # 최적의 모델 state_dict 반환
    return best_model_state_dict

In [17]:
# 학습 시작
train_losses_epoch = []  # epoch 별 train_loss 기록을 위한 리스트
train_accs_epoch = []  # epoch 별 train_accuracy 기록을 위한 리스트
for epoch in range(num_epochs):
    train_losses, train_accs = train_fn(train_dataloader, model, optimizer, device)
    train_losses_epoch.extend(train_losses)
    train_accs_epoch.extend(train_accs)
    # 일정한 간격으로 체크포인트 저장
    if epoch % 2 == 0 and epoch > 0:
        checkpoint = {
            'epoch': epoch,
            'model_state_dict': model.state_dict(),
            'optimizer_state_dict': optimizer.state_dict(),
            # 필요한 경우 추가 정보 저장 (예: loss, accuracy 등)
        }
        torch.save(checkpoint, f'checkpoint_epoch_{epoch}.pth')

Training: 100%|██████████| 6577/6577 [36:13<00:00,  3.03it/s, Loss=0.101, Accuracy=0.974] 


In [18]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# 시각화
fig = make_subplots(rows=1, cols=2, subplot_titles=("Train Loss", "Train Accuracy"))

# Loss 그래프
fig.add_trace(
    go.Scatter(x=list(range(len(train_losses_epoch))), y=train_losses_epoch, mode='lines', name='Train Loss'),
    row=1, col=1
)
fig.update_xaxes(title_text="Iterations", row=1, col=1)
fig.update_yaxes(title_text="Loss", row=1, col=1)

# Accuracy 그래프
fig.add_trace(
    go.Scatter(x=list(range(len(train_accs_epoch))), y=train_accs_epoch, mode='lines', name='Train Accuracy'),
    row=1, col=2
)
fig.update_xaxes(title_text="Iterations", row=1, col=2)
fig.update_yaxes(title_text="Accuracy", row=1, col=2)

fig.update_layout(title="Training Progress", showlegend=False)
fig.show()

In [19]:
# 모델의 상태 딕셔너리를 얻어옵니다.
model_state_dict = model.state_dict()

# 모델 상태 딕셔너리를 파일로 저장합니다.
torch.save(model_state_dict, "model_state_dict_epoch2.pt")

# 옵티마이저의 상태 딕셔너리를 얻어옵니다.
optimizer_state_dict = optimizer.state_dict()

# 옵티마이저 상태 딕셔너리를 파일로 저장합니다.
torch.save(optimizer_state_dict, "optimizer_state_dict_epoch2.pt")

In [20]:
# 검증 데이터로 평가 수행
val_accuracy = eval_fn(val_dataloader, model, device)
print("Validation Accuracy:", val_accuracy)

Predicted Labels: [2 0 2 ... 2 0 2]
True Labels: [2 0 2 ... 2 0 2]
Validation Accuracy: 0.9018968695949671


In [21]:
# 한국어 문장을 입력으로 받아서 예측 라벨을 출력하는 함수
def predict_label(sentence, model, tokenizer, device):
    model.eval()
    with torch.no_grad():
        inputs = tokenizer(sentence, return_tensors='pt', truncation=True, padding=True)
        inputs = {k: v.to(device) for k, v in inputs.items()}
        outputs = model(**inputs)
        logits = outputs.logits
        predicted_label = torch.argmax(logits, dim=1).item()
        return predicted_label

In [26]:
df = pd.read_csv("../dataset/사랑이별_커뮤니티_챗봇데이터.csv", encoding='UTF-8')

In [27]:
# 한국어 문장 입력 받기
korean_sentences = df['sentence'].tolist()

# 예측 라벨 출력
emotion_labels = {0:'부정', 1:'중립', 2:'긍정'}
predicted_label = [emotion_labels[predict_label(korean_sentence, model, tokenizer, device)] for korean_sentence in tqdm(korean_sentences)]
df['label'] = predicted_label

100%|██████████| 11823/11823 [02:57<00:00, 66.60it/s]


In [ ]:
predicted_label

In [28]:
# 데이터프레임을 한 줄씩 돌면서 처리
sentiment2 = []
for index, row in tqdm(df.iterrows()):
    sentiment_value = row['sentiment']
    label_value = row['label']
    
    # sentiment 값이 0일 때 처리
    if sentiment_value == 0:
        if label_value == 'positive':
            sentiment2.append("기쁨")
        elif label_value == 'negative':
            sentiment2.append("슬픔")
        else:
            sentiment2.append("중립")

    elif sentiment_value == 1:
        if label_value == 'positive':
            sentiment2.append("기쁨")
        elif label_value == 'negative':
            sentiment2.append("슬픔")
        else:
            sentiment2.append("중립")
    else:
        if label_value == 'positive':
            sentiment2.append("기쁨")
        elif label_value == 'negative':
            sentiment2.append("슬픔")
        else:
            sentiment2.append("중립")

df['sentiment'] = sentiment2
df = df[['sentence', 'sentiment']]
df.to_csv("../dataset/사랑이별_커뮤니티_챗봇데이터_전처리완.csv", index=False, encoding='UTF-8')

11823it [00:00, 24199.16it/s]
